*Author: Mai Linh Luong*

#Introduction
In this notebook, you will find how the categorization of the steps was done and the map of the route of the running sesion from test person 2. 

In [33]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [34]:
#import the necessary libraries
import numpy as np

import matplotlib.pyplot as plt
from matplotlib.patches import Patch

import pandas as pd

#kepler
import keplergl

## Dataset
The following dataset are going to be used within this notebook. 

In [35]:
df_impact_sa = pd.read_csv('/content/drive/MyDrive/ICT Fontys/Semester 7/Project/P2 - Cleaned Own Version/tp2-owncleaned')
df_impact = pd.read_csv('/content/drive/MyDrive/ICT Fontys/Groupprojects/Semester 7/Mini Company - FR Corp/1.Projects/Music/2.Exploratory Data Analysis/Datasets/TestRunnerTwo/testperson2.csv')
location = pd.read_csv('/content/drive/MyDrive/ICT Fontys/Groupprojects/Semester 7/Mini Company - FR Corp/1.Projects/Music/2.Exploratory Data Analysis/Datasets/TestRunnerTwo/phone_location.csv')
music = pd.read_csv('/content/drive/MyDrive/ICT Fontys/Groupprojects/Semester 7/Mini Company - FR Corp/1.Projects/Music/2.Exploratory Data Analysis/Datasets/TestRunnerTwo/music.csv')

# Categorize the Running for Test Person 2

According to the article of triatlete, stomping hard on the ground while running (so high impact) could be doing real damage. So that means that high impact would be considered as bad running.

source: https://www.triathlete.com/training/dont-pavement-pounder/

## 1.Impact 

In [36]:
df_impact.describe()

index    pronation  ...     duration     position
count  6380.000000  6380.000000  ...  6380.000000  6380.000000
mean   6591.333856   -12.206364  ...  2448.945929   212.140552
std    1924.569348     2.040882  ...     0.000000   143.927321
min    3262.000000   -19.200000  ...  2448.945929     0.055000
25%    4917.750000   -13.600000  ...  2448.945929    89.229000
50%    6592.500000   -12.100000  ...  2448.945929   209.227000
75%    8254.250000   -10.600000  ...  2448.945929   329.227000
max    9920.000000    -7.600000  ...  2448.945929   569.225000

[8 rows x 14 columns]

In [37]:
#let's see how many values we are missing
df_impact.isnull().sum()

index           0
t               0
foot            0
pronation       0
braking         0
impact          0
contact_time    0
flight_ratio    0
strike          0
power           0
date            0
time            0
timediff        0
frequency       0
cadence         0
speed           0
session_id      0
duration        0
track_uri       0
paused          0
artist          0
track           0
context_uri     0
context         0
position        0
dtype: int64

In [38]:
df_impact.describe()

index    pronation  ...     duration     position
count  6380.000000  6380.000000  ...  6380.000000  6380.000000
mean   6591.333856   -12.206364  ...  2448.945929   212.140552
std    1924.569348     2.040882  ...     0.000000   143.927321
min    3262.000000   -19.200000  ...  2448.945929     0.055000
25%    4917.750000   -13.600000  ...  2448.945929    89.229000
50%    6592.500000   -12.100000  ...  2448.945929   209.227000
75%    8254.250000   -10.600000  ...  2448.945929   329.227000
max    9920.000000    -7.600000  ...  2448.945929   569.225000

[8 rows x 14 columns]

The range of `impact` goes from 4.687500 and 13.687500. This range will be divided into 4 sections where each will be labeled. The lower the impact, the better the running performance.  

2.25

- 4.687500 to 6.9375 = very good running
- 6.9375 to 9.1875 = good running
- 9.1875 to 11.4375  = bad running
- 11.4375 to 13.687500 = very bad running

In [39]:
# create a list of our category
runcat = [ 
    (df_impact['impact'] <= 4.687500), 
    (df_impact['impact'] > 4.687500) & (df_impact['impact'] <= 6.9375),
    (df_impact['impact'] > 6.9375) & (df_impact['impact'] <=  9.1875),
    (df_impact['impact'] > 9.1875) & (df_impact['impact'] <= 11.4375), 
    (df_impact['impact'] > 11.4375) & (df_impact['impact'] <= 13.687500)
    ]

# create a list of the values we want to assign for each condition
runvalues = ['very good running', 'very good running', 'good running', 'bad running', 'very bad running']

# create a new column and use np.select to assign values to it using our lists as arguments
df_impact['run_category'] = np.select(runcat, runvalues)

# display updated DataFrame
df_impact.head(5)

index                              t  ... position  run_category
0   3262  2020-06-07 18:46:18.758389950  ...  176.704  good running
1   3263  2020-06-07 18:46:18.975515842  ...  176.704  good running
2   3264  2020-06-07 18:46:19.387653828  ...  176.704  good running
3   3265  2020-06-07 18:46:19.843976974  ...    0.119  good running
4   3267  2020-06-07 18:46:20.446063042  ...    0.119  good running

[5 rows x 26 columns]

In [40]:
#count the amount of categories
run_count = df_impact['run_category'].value_counts().reset_index()
run_count

index  run_category
0       good running          3619
1  very good running          1548
2        bad running           962
3   very bad running           251

In [41]:
#count the amount of categories
run_count = df_impact['run_category'].value_counts().reset_index()
run_count

index  run_category
0       good running          3619
1  very good running          1548
2        bad running           962
3   very bad running           251

### 1.1 Plot Run Category

In [42]:
import plotly.express as px

#visualisation amount of bad/good running

run_count.columns = ['Category', 'Total']

fig = px.bar(run_count, x= 'Category', y = 'Total', color = 'Category',
             title="Total category of running")
fig.show()

## 2.Impact Symmetry Angle

In [43]:
#shorten the dataset
df_impact_sa = df_impact_sa[["t", "pronation_sa", "braking_sa", "impact_sa", "contact_time_sa", "strike_sa", "power_sa", "initial_foot", 'cadence_sa', "frequency_sa", "track_uri"]]

#show shape of the dataset
df_impact_sa.shape

(101121, 11)

In [44]:
#let's see how many values we are missing
df_impact_sa.isnull().sum()

t                     0
pronation_sa       2855
braking_sa         2855
impact_sa          2855
contact_time_sa    2855
strike_sa          2855
power_sa           2855
initial_foot          0
cadence_sa         2855
frequency_sa       2855
track_uri             0
dtype: int64

In [45]:
#now we are going to drop all the null values
df_impact_sa = df_impact_sa.dropna()

In [46]:
df_impact_sa.describe()

pronation_sa    braking_sa  ...    cadence_sa  frequency_sa
count  98266.000000  98266.000000  ...  98266.000000  98266.000000
mean      -0.081800     -0.008425  ...      0.000029      0.003356
std        0.031523      0.056445  ...      0.001413      0.115083
min       -0.189008     -0.180100  ...     -0.023000     -0.298845
25%       -0.102939     -0.048875  ...      0.000000     -0.081524
50%       -0.082189     -0.011435  ...      0.000000      0.007787
75%       -0.061589      0.025745  ...      0.000000      0.096763
max        0.043095      0.176557  ...      0.043339      0.326089

[8 rows x 8 columns]

Let's say 0 is the absolute line where every value below 0 would be considered as good running and values above 0 would be considered as bad running. 

The range of `impact_sa` goes from -0.171791 and 0.173803. This range will be divided into 4 sections with 0 as the middle line. 

- -0.171791 to -0.0858955 = very good running
- -0.0858955 to 0 = good running
- 0 to 0.0869015  = bad running
- 0.0869015 to 0.173803 = very bad running

In [47]:
# create a list of our category
runcat = [ 
    (df_impact_sa['impact_sa'] <= -0.171791), 
    (df_impact_sa['impact_sa'] > -0.171791) & (df_impact_sa['impact_sa'] < -0.0858955),
    (df_impact_sa['impact_sa'] > -0.0858955) & (df_impact_sa['impact_sa'] <=  0),
    (df_impact_sa['impact_sa'] > 0) & (df_impact_sa['impact_sa'] <= 0.0869015), 
    (df_impact_sa['impact_sa'] > 0.0869015) & (df_impact_sa['impact_sa'] < 0.173803)
    ]

# create a list of the values we want to assign for each condition
runvalues = ['very good running', 'very good running', 'good running', 'bad running', 'very bad running']

# create a new column and use np.select to assign values to it using our lists as arguments
df_impact_sa['run_category'] = np.select(runcat, runvalues)

# display updated DataFrame
df_impact_sa.head(5)

t  ...  run_category
12  2020-06-07 18:46:18.975515842  ...  good running
13  2020-06-07 18:46:18.975515842  ...  good running
14  2020-06-07 18:46:18.975515842  ...  good running
15  2020-06-07 18:46:18.975515842  ...  good running
16  2020-06-07 18:46:18.975515842  ...  good running

[5 rows x 12 columns]

In [48]:
#count the amount of categories
run_count_sa = df_impact_sa['run_category'].value_counts().reset_index()
run_count_sa

index  run_category
0       good running         49224
1        bad running         34319
2  very good running          8718
3   very bad running          6005

In [49]:
import plotly.express as px

#visualisation amount of bad/good running

run_count_sa.columns = ['Category', 'Total']

fig = px.bar(run_count_sa, x= 'Category', y = 'Total', color = 'Category',
             title="Total category of running")
fig.show()

###2.1 Plot Run Category
Now we are going to visualise the count of the amount of run categories. This way, we have an overview of the performance of the running session. 

In [50]:
import plotly.express as px

#visualisation amount of bad/good running

run_count_sa.columns = ['Category', 'Total']

fig = px.bar(run_count_sa, x= 'Category', y = 'Total', color = 'Category',
             title="Total category of running")
fig.show()

## 3.Results

As you can see above, the two plots quite differs from each other. You would say that in the first plot (of the impact) the runner did quite a good job on the running performance. His running performance based on the impact (so the first plot) would be better than based on the impact symmetry angle. 

However, the article of triatlete only mentions the impact and nothing about the symmetry angle. This means, based on the article, the first option would be considered as more trustworthy. 

# Kepler Map Test Person 2

In this chapter, we are going to plot the route that the test person ran. This way we can see, on which route the test person was stomping hard (so highlighting the bad running patterns). 

In [51]:
#install kepler 
# !pip install keplergl

## 1.Merge the location dataset
In order to create a map, merging df_impact and location need to be done. 

In [58]:
df_impact.shape

(6380, 26)

In [60]:
location.shape

(3110, 10)

In [61]:
#convert the two datatype in datetime
location['t'] = pd.to_datetime(location['t'])
df_impact['t'] = pd.to_datetime(df_impact['t'])

In [62]:
#merge the two dataset based on the nearest time
df = pd.merge_asof(df_impact, location, on='t', direction = 'nearest')

In [63]:
df.shape

(6380, 35)

##2.Kepler Map Visualisation

In [70]:
from google.colab import output
output.enable_custom_widget_manager()

In [73]:
#get the longest session
df_longest = df.groupby("session_id")['duration'].max().reset_index()

#session 15FB2F71-7F56-4434-8A3B-127A14E966B2	is the longest

df_longest = df[(df['session_id'] == '15FB2F71-7F56-4434-8A3B-127A14E966B2')].reset_index()

In [74]:
# Load a map with data and config and height
from keplergl import KeplerGl
map_2 = KeplerGl(height=800, data={"lonlat_acc": df_longest})
map_2

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


KeplerGl(data={'lonlat_acc':       level_0  index  ...   speed_y speed_acc
0           0   3262  ...  2.626934…

## 3. Result
As you can see above, it's shown that the bad running part of the test person, happened mostly where the runner had to make turns. We can also see from the map when we put in the filter "very good running" that the runner had a stable running impact throughout the session. 